In [1]:
from os import path
import os
import pandas as pd
import requests, zipfile, io, os
from zipfile import BadZipfile
from zipfile import ZipFile
import shutil
import glob
import numpy as np
pd.set_option('display.max_colwidth', -1)

/var/folders/mk/7yynft554x38v3t6f_65fkzc0000gn/T/ipykernel_22460/64196590.py:10: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('display.max_colwidth', -1)


In [2]:
df = pd.read_csv('AllRegion_EPWLinks.csv', index_col=0) 
df

Location Name  \
0      Vernadsky.Research.Base-Argentine.Islands GBR ATA         
1      Esperanza.Base-Hope.Bay ARG ATA                           
2      Esperanza.Base-Hope.Bay ARG ATA                           
3      Esperanza.Base-Hope.Bay ARG ATA                           
4      Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   
...                                                        ...   
45935  Old Crow RCS YT CAN                                       
45936  Rock River YT CAN                                         
45937  Teslin AUT YT CAN                                         
45938  Watson Lake AP YT CAN                                     
45939  Whitehorse AP YT CAN                                      

                              Coordinates  \
0      ['-64.26700', '-65.25000', '9.0']    
1      ['-56.99730', '-63.39810', '3.0']    
2      ['-56.99730', '-63.39810', '3.0']    
3      ['-56.99730', '-63.39810', '3.0']    
4      ['-44.73300', '-60.73300', '8.0']    
...                                  ...    
45935  ['-139.8400', '67.57000', '251.2']   
45936  ['-136.2200', '66.98000', '731.0']   
45937  ['-132.7300', '60.17000', '705.0']   
45938  ['-128.8200', '60.12000', '687.3']   
45939  ['-135.0700', '60.71000', '706.2']   

                                                                                                                                                  URL for files  
0      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_GBR_Vernadsky.Research.Base-Argentine.Islands.889520_TMYx.zip                  
1      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2004-2018.zip                          
2      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2007-2021.zip                          
3      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.zip                                    
4      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2004-2018.zip  
...                                                                                                                                                         ...  
45935  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/YT_Yukon/CAN_YT_Old.Crow.RCS.710440_CWEC2020.zip                        
45936  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/YT_Yukon/CAN_YT_Rock.River.715060_CWEC2020.zip                          
45937  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/YT_Yukon/CAN_YT_Teslin.AUT.710450_CWEC2020.zip                          
45938  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/YT_Yukon/CAN_YT_Watson.Lake.AP.711990_CWEC2020.zip                      
45939  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/YT_Yukon/CAN_YT_Whitehorse.AP.719640_CWEC2020.zip                       

[45940 rows x 3 columns]

In [3]:
#df['zip'] = df['URL for files'].str.split('/').str[-1]
#df['zip']

In [4]:
df['WMO'] = df['URL for files'].str.split('/').str[-1].str.extract('(\d+)')
df['WMO'] = df['WMO'].fillna(0)
df['WMO'] =df['WMO'].astype(str).astype(int)

df['WMO'].dtypes

dtype('int64')

In [5]:
df['last_year'] = df['URL for files'].str.split('/').str[-1].str.split('.').str[-2].str.split('-').str[-1]
df['last_year'] = df['last_year'].astype('string')
df['last_year'] = df['last_year'].str[-4:]

df['last_year'].head()

0    TMYx
1    2018
2    2021
3    TMYx
4    2018
Name: last_year, dtype: string

In [9]:
df.head()

Location Name  \
0  Vernadsky.Research.Base-Argentine.Islands GBR ATA         
1  Esperanza.Base-Hope.Bay ARG ATA                           
2  Esperanza.Base-Hope.Bay ARG ATA                           
3  Esperanza.Base-Hope.Bay ARG ATA                           
4  Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   

                         Coordinates  \
0  ['-64.26700', '-65.25000', '9.0']   
1  ['-56.99730', '-63.39810', '3.0']   
2  ['-56.99730', '-63.39810', '3.0']   
3  ['-56.99730', '-63.39810', '3.0']   
4  ['-44.73300', '-60.73300', '8.0']   

                                                                                                                                              URL for files  \
0  https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_GBR_Vernadsky.Research.Base-Argentine.Islands.889520_TMYx.zip                   
1  https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2004-2018.zip                           
2  https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2007-2021.zip                           
3  https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.zip                                     
4  https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2004-2018.zip   

      WMO last_year  
0  889520  TMYx      
1  889630  2018      
2  889630  2021      
3  889630  TMYx      
4  889680  2018

In [10]:
def download_file(url):
    headers=   {"Auth": "{abcd}", 
                "accept": "*/*",               
               "accept-encoding": "gzip;deflate;br" }
    response = requests.request("GET", url, headers = headers)
    filename = os.getcwd()+'/downloads_EPW/'
    #filename = os.getcwd()+'/test_epw/'
    try:
        with ZipFile(io.BytesIO(response.content)) as z:
            print("zipfile is OK")
            #z = zipfile.ZipFile(io.BytesIO(response.content))
            z_files = z.namelist()
            #print(z_files)
            extension = '.epw'
            epw = [file for file in z_files if os.path.splitext(file)[1] == extension]
            epwName= epw[0]
            print(epwName)
            z.extract(epw[0],filename)
            #print(epw[0])
            #print(filename)
            #z.extractall(filename)
    except BadZipfile:
        print('Download did not work')
        epwName = "N/A"
    return response.status_code, epwName



In [11]:
## Read in an EPW file to a Pandas dataframe
def readEPW(path):
    # Read the location
    df = pd.read_csv(path, nrows=1, header=None,encoding_errors='ignore') # Read only the first row
    latitude = df.iloc[0, 6]
    longitude = df.iloc[0, 7]
    timezone = df.iloc[0, 8]
    
    # Read the hourly data
    df = pd.read_csv(path, skiprows=range(8), header=None,encoding_errors='ignore') # Read the file, skip the 8 header rows
    # There are no column names in the file. We need to assign them.
    df.columns = ['Year', 'Month', 'Day', 'Hour', 'Minute', 'Data Source and Uncertainty Flags',
                  'Dry Bulb Temperature', 'Dew Point Temperature', 'Relative Humidity', 'Atmospheric Station Pressure',
                  'Extraterrestrial Horizontal Radiation', 'Extraterrestrial Direct Normal Radiation', 'Horizontal Infrared Radiation Intensity',
                  'Global Horizontal Radiation', 'Direct Normal Radiation', 'Diffuse Horizontal Radiation',
                  'Global Horizontal Illuminance', 'Direct Normal Illuminance', 'Diffuse Horizontal Illuminance', 'Zenith Luminance',
                  'Wind Direction', 'Wind Speed', 'Total Sky Cover', 'Opaque Sky Cover', 'Visibility', 'Ceiling Height',
                  'Present Weather Observation', 'Present Weather Codes', 'Precipitable Water', 'Aerosol Optical Depth',
                  'Snow Depth', 'Days Since Last Snowfall', 'Albedo', 'Liquid Precipitation Depth', 'Liquid Precipitation Quantity']
    return df

In [12]:
## Read in an EPW file to a Pandas dataframe
def readEPW_DesignDay(path):
    # Read the location
    df = pd.read_csv(path, nrows=1, header=None,encoding_errors='ignore') # Read only the first row
    latitude = df.iloc[0, 6]
    longitude = df.iloc[0, 7]
    timezone = df.iloc[0, 8]
    
    # Read the hourly data
    df = pd.read_csv(path, skiprows=range(8), header=None,encoding_errors='ignore') # Read the file, skip the 8 header rows
    # There are no column names in the file. We need to assign them.
    df.columns = ['Year', 'Month', 'Day', 'Hour', 'Minute', 'Data Source and Uncertainty Flags',
                  'Dry Bulb Temperature', 'Dew Point Temperature', 'Relative Humidity', 'Atmospheric Station Pressure',
                  'Extraterrestrial Horizontal Radiation', 'Extraterrestrial Direct Normal Radiation', 'Horizontal Infrared Radiation Intensity',
                  'Global Horizontal Radiation', 'Direct Normal Radiation', 'Diffuse Horizontal Radiation',
                  'Global Horizontal Illuminance', 'Direct Normal Illuminance', 'Diffuse Horizontal Illuminance', 'Zenith Luminance',
                  'Wind Direction', 'Wind Speed', 'Total Sky Cover', 'Opaque Sky Cover', 'Visibility', 'Ceiling Height',
                  'Present Weather Observation', 'Present Weather Codes', 'Precipitable Water', 'Aerosol Optical Depth',
                  'Snow Depth', 'Days Since Last Snowfall', 'Albedo', 'Liquid Precipitation Depth', 'Liquid Precipitation Quantity']
    
    htg_996_epw= df['Dry Bulb Temperature'].quantile(q=0.004)
    htg_990_epw= df['Dry Bulb Temperature'].quantile(q=0.010)
    clg_004_epw= df['Dry Bulb Temperature'].quantile(q=0.996)
    clg_010_epw= df['Dry Bulb Temperature'].quantile(q=0.99)
    return htg_996_epw,htg_990_epw,clg_004_epw,clg_010_epw

In [14]:
#import DD data
df_DD = pd.read_csv('Climate Data 2021_SI_Rev.csv') 
df_DD

Country State/Province              Station     WMO  \
0     Svalbard and Jan Mayen  NaN            JAN MAYEN            10010    
1     Svalbard and Jan Mayen  NaN            HORNSUND             10030    
2     Norway                  NaN            EDGEOYA              10060    
3     Svalbard and Jan Mayen  NaN            NY-ALESUND           10070    
4     Svalbard and Jan Mayen  NaN            SVALBARD             10080    
...                      ...  ...                 ...               ...    
9232  USA                     MI             WEST NEEBISH ISLAND  998203   
9233  USA                     SC             LAKE WATEREE         998208   
9234  USA                     NC             DUCK PIER            998209   
9235  USA                     NY             NIAGARA INTAKE       998235   
9236  USA                     AK             NOKOLSKI             998429   

       WBAN  Latitude Longitude  Heating DB 99.6%  Heating DB 99%  \
0     99999  70.940N   8.668W   -14.0             -11.8             
1     99999  77.000N   15.500E  -22.1             -20.5             
2     99999  78.251N   22.823E  -28.0             -25.7             
3     99999  78.9228N  11.9331E -25.2             -22.7             
4     99999  78.246N   15.466E  -28.5             -25.8             
...     ...      ...       ...    ...               ...             
9232  99999  46.2847N  84.2098W -25.6             -22.4             
9233  99999  34.335N   80.702W  -5.5              -3.5              
9234  99999  36.184N   75.746W  -4.2              -2.1              
9235  99999  43.0770N  79.0140W -15.5             -13.1             
9236  99999  52.941N   168.871W -5.6              -4.1              

      Cooling DB 0.4%  ...  Cooling DB 1%  Cooling MCWB 1%  Cooling DB 2%  \
0     9.6              ...  8.9            7.7              8.4             
1     8.1              ...  7.2            5.6              6.6             
2     9.2              ...  8.1            6.5              7.1             
3     9.9              ...  8.7            6.1              7.9             
4     11.9             ...  10.5           7.5              9.4             
...    ...             ...   ...           ...              ...             
9232  27.9             ...  26.3          NaN               24.8            
9233  36.8             ...  35.4          NaN               34.1            
9234  31.4             ...  30.2          NaN               29.1            
9235  28.9             ...  27.7          NaN               26.6            
9236  13.9             ...  12.9          NaN               12.3            

      Cooling MCWB 2%  Evaporation WB 0.4%  Evaporation MCDB 0.4%  \
0     7.4              8.6                  9.2                     
1     5.2              6.6                  7.5                     
2     5.7              7.5                  8.9                     
3     5.6              7.3                  9.3                     
4     6.9              8.7                  11.1                    
...   ...              ...                   ...                    
9232 NaN              NaN                  NaN                      
9233 NaN              NaN                  NaN                      
9234 NaN              NaN                  NaN                      
9235 NaN              NaN                  NaN                      
9236 NaN              NaN                  NaN                      

      Evaporation WB 1%  Evaporation MCDB 1%  Evaporation WB 2%  \
0     8.1                8.7                  7.7                 
1     6.0                6.8                  5.5                 
2     6.6                7.9                  5.8                 
3     6.5                8.4                  5.8                 
4     7.8                9.8                  7.1                 
...   ...                ...                  ...                 
9232 NaN                NaN                  NaN        

In [15]:
df_summary = df.merge(df_DD, how='inner', on='WMO')
df_summary

Location Name  \
0      Esperanza.Base-Hope.Bay ARG ATA                           
1      Esperanza.Base-Hope.Bay ARG ATA                           
2      Esperanza.Base-Hope.Bay ARG ATA                           
3      Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   
4      Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   
...                                                        ...   
30458  Montreal-Mirabel Intl AP QC CAN                           
30459  Slave Lake AB CAN                                         
30460  Wainwright CFB Airfield AB CAN                            
30461  Grand Etang NS CAN                                        
30462  Malay Falls NS CAN                                        

                              Coordinates  \
0      ['-56.99730', '-63.39810', '3.0']    
1      ['-56.99730', '-63.39810', '3.0']    
2      ['-56.99730', '-63.39810', '3.0']    
3      ['-44.73300', '-60.73300', '8.0']    
4      ['-44.73300', '-60.73300', '8.0']    
...                                  ...    
30458  ['-74.03860', '45.68060', '82.3']    
30459  ['-114.7800', '55.29000', '582.8']   
30460  ['-111.1000', '52.83000', '686.3']   
30461  ['-61.05000', '46.55000', '12.5']    
30462  ['-62.48000', '44.98000', '39.6']    

                                                                                                                                                  URL for files  \
0      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2004-2018.zip                           
1      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2007-2021.zip                           
2      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.zip                                     
3      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2004-2018.zip   
4      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2007-2021.zip   
...                                                                                                                                                         ...   
30458  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/QC_Quebec/CAN_QC_Montreal-Mirabel.Intl.AP.719050_CWEC2016.zip            
30459  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/AB_Alberta/CAN_AB_Slave.Lake.713690_CWEC2020.zip                         
30460  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/AB_Alberta/CAN_AB_Wainwright.CFB.Airfield.711180_CWEC2020.zip            
30461  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NS_Nova_Scotia/CAN_NS_Grand.Etang.730300_CWEC2020.zip                    
30462  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NS_Nova_Scotia/CAN_NS_Malay.Falls.730290_CWEC2020.zip                    

          WMO last_year     Country State/Province         Station   WBAN  \
0      889630  2018      Antarctica  NaN            BASE ESPERANZA  99999   
1      889630  2021      Antarctica  NaN            BASE ESPERANZA  99999   
2      889630  TMYx      Antarctica  NaN            BASE ESPERANZA  99999   
3      889680  2018      Antarctica  NaN            BASE ORCADAS    99999   
4      889680  2021      Antarctica  NaN            BASE ORCADAS    99999   
...       ...   ...             ...  ...                     ...      ...   
30458  719050  2016      Canada      QC             KUUJJUARAPIK    99999   
30459  713690  2020      Canada      AB             SLAVE LAKE      99999   
30460  711180  2020      Canada      AB             WAINWRIGHT CF

In [16]:
s_htg_996_epw= []
s_htg_990_epw= []
s_clg_004_epw= []
s_clg_010_epw= []

counter =-1
#for url in df_summary['URL for files']:
for index in df_summary.index:
    if index > counter:
        #print(index)
        print(counter)
        counter=counter+1
        url = df_summary.loc[index,'URL for files']
        print(url)
        status, epwpath = download_file(url)
        print(status, epwpath)
        if status ==  200:
            htg_996,htg_990,clg_004,clg_010 = readEPW_DesignDay(path.join('downloads_EPW/',epwpath))
            #print(htg_996,htg_990,clg_004,clg_010)
            s_htg_996_epw.append(htg_996)
            s_htg_990_epw.append(htg_990)
            s_clg_004_epw.append(clg_004)
            s_clg_010_epw.append(clg_010)
            os.remove(path.join('downloads_EPW/',epwpath))
        else:
            s_htg_996_epw.append("N/A")
            s_htg_990_epw.append("N/A")
            s_clg_004_epw.append("N/A")
            s_clg_010_epw.append("N/A")
        continue

0
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2007-2021.zip
zipfile is OK
ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2007-2021.epw
200 ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2007-2021.epw
1
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.zip
zipfile is OK
ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.epw
200 ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.epw
2
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2004-2018.zip
zipfile is OK
ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2004-2018.epw
200 ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2004-2018.epw
3
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2007-2021.zip
zipfile 

zipfile is OK
ATA_CHL_Eduardo.Frei.Montalva.AWS-Feldes.Peninsula-King.Ge.890560_TMYx.2007-2021.epw
200 ATA_CHL_Eduardo.Frei.Montalva.AWS-Feldes.Peninsula-King.Ge.890560_TMYx.2007-2021.epw
34
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_CHL_Eduardo.Frei.Montalva.AWS-Feldes.Peninsula-King.Ge.890560_TMYx.zip
zipfile is OK
ATA_CHL_Eduardo.Frei.Montalva.AWS-Feldes.Peninsula-King.Ge.890560_TMYx.epw
200 ATA_CHL_Eduardo.Frei.Montalva.AWS-Feldes.Peninsula-King.Ge.890560_TMYx.epw
35
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_CHL_Captain.Arturo.Prat.Navy.Base.890570_TMYx.2004-2018.zip
zipfile is OK
ATA_CHL_Captain.Arturo.Prat.Navy.Base.890570_TMYx.2004-2018.epw
200 ATA_CHL_Captain.Arturo.Prat.Navy.Base.890570_TMYx.2004-2018.epw
36
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_CHL_Captain.Arturo.Prat.Navy.Base.890570_TMYx.2007-2021.zip
zipfile is OK
ATA_CHL_Captain.Arturo.Prat.Navy.Base.890570_TMYx.2007-2021

zipfile is OK
ATA_GBR_Sky.Blu.AWS.892720_TMYx.epw
200 ATA_GBR_Sky.Blu.AWS.892720_TMYx.epw
68
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_USA_U-Wisc-Theresa.AWS-West.Antarctica.893140_TMYx.2007-2021.zip
zipfile is OK
ATA_USA_U-Wisc-Theresa.AWS-West.Antarctica.893140_TMYx.2007-2021.epw
200 ATA_USA_U-Wisc-Theresa.AWS-West.Antarctica.893140_TMYx.2007-2021.epw
69
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_USA_U-Wisc-Theresa.AWS-West.Antarctica.893140_TMYx.zip
zipfile is OK
ATA_USA_U-Wisc-Theresa.AWS-West.Antarctica.893140_TMYx.epw
200 ATA_USA_U-Wisc-Theresa.AWS-West.Antarctica.893140_TMYx.epw
70
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_USA_Mount.Siple.893270_TMYx.2007-2021.zip
zipfile is OK
ATA_USA_Mount.Siple.893270_TMYx.2007-2021.epw
200 ATA_USA_Mount.Siple.893270_TMYx.2007-2021.epw
71
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_USA_Mount.Siple.893270_TMYx.zip
zi

zipfile is OK
ATA_AUS_Casey.Research.Stn-Wilkes.Land.896110_TMYx.epw
200 ATA_AUS_Casey.Research.Stn-Wilkes.Land.896110_TMYx.epw
100
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_FRA_Dumont.d-Urville.Stn-Adelie.Land.896420_TMYx.2004-2018.zip
zipfile is OK
ATA_FRA_Dumont.d-Urville.Stn-Adelie.Land.896420_TMYx.2004-2018.epw
200 ATA_FRA_Dumont.d-Urville.Stn-Adelie.Land.896420_TMYx.2004-2018.epw
101
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_FRA_Dumont.d-Urville.Stn-Adelie.Land.896420_TMYx.2007-2021.zip
zipfile is OK
ATA_FRA_Dumont.d-Urville.Stn-Adelie.Land.896420_TMYx.2007-2021.epw
200 ATA_FRA_Dumont.d-Urville.Stn-Adelie.Land.896420_TMYx.2007-2021.epw
102
https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_FRA_Dumont.d-Urville.Stn-Adelie.Land.896420_TMYx.zip
zipfile is OK
ATA_FRA_Dumont.d-Urville.Stn-Adelie.Land.896420_TMYx.epw
200 ATA_FRA_Dumont.d-Urville.Stn-Adelie.Land.896420_TMYx.epw
103
https://climate.

zipfile is OK
ALA_KM_Kumlinge.027900_TMYx.epw
200 ALA_KM_Kumlinge.027900_TMYx.epw
138
https://climate.onebuilding.org/WMO_Region_6_Europe/ALA_Aland_Islands/ALA_MH_Jomala-Mariehamn.AP.029700_TMYx.2004-2018.zip
zipfile is OK
ALA_MH_Jomala-Mariehamn.AP.029700_TMYx.2004-2018.epw
200 ALA_MH_Jomala-Mariehamn.AP.029700_TMYx.2004-2018.epw
139
https://climate.onebuilding.org/WMO_Region_6_Europe/ALA_Aland_Islands/ALA_MH_Jomala-Mariehamn.AP.029700_TMYx.2007-2021.zip
zipfile is OK
ALA_MH_Jomala-Mariehamn.AP.029700_TMYx.2007-2021.epw
200 ALA_MH_Jomala-Mariehamn.AP.029700_TMYx.2007-2021.epw
140
https://climate.onebuilding.org/WMO_Region_6_Europe/ALA_Aland_Islands/ALA_MH_Jomala-Mariehamn.AP.029700_TMYx.zip
zipfile is OK
ALA_MH_Jomala-Mariehamn.AP.029700_TMYx.epw
200 ALA_MH_Jomala-Mariehamn.AP.029700_TMYx.epw
141
https://climate.onebuilding.org/WMO_Region_6_Europe/ALA_Aland_Islands/ALA_KK_Bogskar.Lighthouse.029790_TMYx.2004-2018.zip
zipfile is OK
ALA_KK_Bogskar.Lighthouse.029790_TMYx.2004-2018.epw
200

...

zipfile is OK
CAN_ON_Gore.Bay-Manitoulin.AP.719560_CWEC2016.epw
200 CAN_ON_Gore.Bay-Manitoulin.AP.719560_CWEC2016.epw
30316
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/ON_Ontario/CAN_ON_Gore.Bay.Climate.719560_CWEC2020.zip
zipfile is OK
CAN_ON_Gore.Bay.Climate.719560_CWEC2020.epw
200 CAN_ON_Gore.Bay.Climate.719560_CWEC2020.epw
30317
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NT_Northwest_Territories/CAN_NT_Inuvik-Zubko.AP.719570_TMYx.2004-2018.zip
zipfile is OK
CAN_NT_Inuvik-Zubko.AP.719570_TMYx.2004-2018.epw
200 CAN_NT_Inuvik-Zubko.AP.719570_TMYx.2004-2018.epw
30318
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NT_Northwest_Territories/CAN_NT_Inuvik-Zubko.AP.719570_TMYx.2007-2021.zip
zipfile is OK
CAN_NT_Inuvik-Zubko.AP.719570_TMYx.2007-2021.epw
200 CAN_NT_Inuvik-Zubko.AP.719570_TMYx.2007-2021.epw
30319
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/

Download did not work
404 N/A
30350
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/YT_Yukon/CAN_YT_Mayo.AP.719650_CWEC2020.zip
zipfile is OK
CAN_YT_Mayo.AP.719650_CWEC2020.epw
200 CAN_YT_Mayo.AP.719650_CWEC2020.epw
30351
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/YT_Yukon/CAN_YT_Dawson.City.AP.719660_TMYx.2004-2018.zip
zipfile is OK
CAN_YT_Dawson.City.AP.719660_TMYx.2004-2018.epw
200 CAN_YT_Dawson.City.AP.719660_TMYx.2004-2018.epw
30352
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/YT_Yukon/CAN_YT_Dawson.City.AP.719660_TMYx.2007-2021.zip
zipfile is OK
CAN_YT_Dawson.City.AP.719660_TMYx.2007-2021.epw
200 CAN_YT_Dawson.City.AP.719660_TMYx.2007-2021.epw
30353
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/YT_Yukon/CAN_YT_Dawson.City.AP.719660_TMYx.zip
zipfile is OK
CAN_YT_Dawson.City.AP.719660_TMYx.epw
200 CAN_YT_Dawson.City.AP.719660_TMYx.epw
303

zipfile is OK
CAN_NU_Cape.Mercy.719750_TMYx.2007-2021.epw
200 CAN_NU_Cape.Mercy.719750_TMYx.2007-2021.epw
30383
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NU_Nunavut/CAN_NU_Cape.Mercy.719750_TMYx.zip
zipfile is OK
CAN_NU_Cape.Mercy.719750_TMYx.epw
200 CAN_NU_Cape.Mercy.719750_TMYx.epw
30384
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NU_Nunavut/CAN_NU_Cape.Mercy.719750_CWEC2020.zip
zipfile is OK
CAN_NU_Cape.Mercy.719750_CWEC2020.epw
200 CAN_NU_Cape.Mercy.719750_CWEC2020.epw
30385
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/QC_Quebec/CAN_QC_Parc.Natl.des.Pingualuit.719760_TMYx.2004-2018.zip
zipfile is OK
CAN_QC_Parc.Natl.des.Pingualuit.719760_TMYx.2004-2018.epw
200 CAN_QC_Parc.Natl.des.Pingualuit.719760_TMYx.2004-2018.epw
30386
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/QC_Quebec/CAN_QC_Parc.Natl.des.Pingualuit.719760_TMYx.2007-2021.zi

zipfile is OK
CAN_NT_Paulatuk-Ruben.AP.719840_TMYx.2007-2021.epw
200 CAN_NT_Paulatuk-Ruben.AP.719840_TMYx.2007-2021.epw
30416
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NT_Northwest_Territories/CAN_NT_Paulatuk-Ruben.AP.719840_TMYx.zip
zipfile is OK
CAN_NT_Paulatuk-Ruben.AP.719840_TMYx.epw
200 CAN_NT_Paulatuk-Ruben.AP.719840_TMYx.epw
30417
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NT_Northwest_Territories/CAN_NT_Paulatuk.719840_CWEC2020.zip
zipfile is OK
CAN_NT_Paulatuk.719840_CWEC2020.epw
200 CAN_NT_Paulatuk.719840_CWEC2020.epw
30418
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NT_Northwest_Territories/CAN_NT_Tuktoyaktuk-Gruben.AP.719850_TMYx.2004-2018.zip
zipfile is OK
CAN_NT_Tuktoyaktuk-Gruben.AP.719850_TMYx.2004-2018.epw
200 CAN_NT_Tuktoyaktuk-Gruben.AP.719850_TMYx.2004-2018.epw
30419
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NT_

zipfile is OK
CAN_SK_Cree.Lake.AP.729200_TMYx.epw
200 CAN_SK_Cree.Lake.AP.729200_TMYx.epw
30449
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NL_Newfoundland_and_Labrador/CAN_NL_Gander.Intl.AP.717420_CWEC.zip
zipfile is OK
CAN_NL_Gander.Intl.AP.717420_CWEC.epw
200 CAN_NL_Gander.Intl.AP.717420_CWEC.epw
30450
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/QC_Quebec/CAN_QC_Montreal-Mirabel.Intl.AP.716278_CWEC.zip
zipfile is OK
CAN_QC_Montreal-Mirabel.Intl.AP.716278_CWEC.epw
200 CAN_QC_Montreal-Mirabel.Intl.AP.716278_CWEC.epw
30451
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/SK_Saskatchewan/CAN_SK_Regina.Intl.AP.715140_CWEC.zip
zipfile is OK
CAN_SK_Regina.Intl.AP.715140_CWEC.epw
200 CAN_SK_Regina.Intl.AP.715140_CWEC.epw
30452
https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/SK_Saskatchewan/CAN_SK_Regina.Intl.AP.715140_CWEC2016.zip
zipfile is OK
CAN_S

In [18]:
df_summary = df_summary.iloc[1: , :]
df_summary

Location Name  \
1      Esperanza.Base-Hope.Bay ARG ATA                           
2      Esperanza.Base-Hope.Bay ARG ATA                           
3      Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   
4      Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   
5      Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   
...                                                        ...   
30458  Montreal-Mirabel Intl AP QC CAN                           
30459  Slave Lake AB CAN                                         
30460  Wainwright CFB Airfield AB CAN                            
30461  Grand Etang NS CAN                                        
30462  Malay Falls NS CAN                                        

                              Coordinates  \
1      ['-56.99730', '-63.39810', '3.0']    
2      ['-56.99730', '-63.39810', '3.0']    
3      ['-44.73300', '-60.73300', '8.0']    
4      ['-44.73300', '-60.73300', '8.0']    
5      ['-44.73300', '-60.73300', '8.0']    
...                                  ...    
30458  ['-74.03860', '45.68060', '82.3']    
30459  ['-114.7800', '55.29000', '582.8']   
30460  ['-111.1000', '52.83000', '686.3']   
30461  ['-61.05000', '46.55000', '12.5']    
30462  ['-62.48000', '44.98000', '39.6']    

                                                                                                                                                  URL for files  \
1      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2007-2021.zip                           
2      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.zip                                     
3      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2004-2018.zip   
4      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2007-2021.zip   
5      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.zip             
...                                                                                                                                               ...             
30458  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/QC_Quebec/CAN_QC_Montreal-Mirabel.Intl.AP.719050_CWEC2016.zip            
30459  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/AB_Alberta/CAN_AB_Slave.Lake.713690_CWEC2020.zip                         
30460  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/AB_Alberta/CAN_AB_Wainwright.CFB.Airfield.711180_CWEC2020.zip            
30461  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NS_Nova_Scotia/CAN_NS_Grand.Etang.730300_CWEC2020.zip                    
30462  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NS_Nova_Scotia/CAN_NS_Malay.Falls.730290_CWEC2020.zip                    

          WMO last_year     Country State/Province         Station   WBAN  \
1      889630  2021      Antarctica  NaN            BASE ESPERANZA  99999   
2      889630  TMYx      Antarctica  NaN            BASE ESPERANZA  99999   
3      889680  2018      Antarctica  NaN            BASE ORCADAS    99999   
4      889680  2021      Antarctica  NaN            BASE ORCADAS    99999   
5      889680  TMYx      Antarctica  NaN            BASE ORCADAS    99999   
...       ...   ...             ...  ...                     ...      ...   
30458  719050  2016      Canada      QC             KUUJJUARAPIK    99999   
30459  713690  2020      Canada      AB             SLAVE LAKE      99999   
30460  711180  2020      Canada      AB             WAINWRIGHT CF

In [19]:
df_summary['Heating DB 99.6% - EPW'] = s_htg_996_epw
df_summary['Heating DB 99% - EPW'] = s_htg_990_epw
df_summary['Cooling DB 0.4% - EPW'] = s_clg_004_epw
df_summary['Cooling DB 1% - EPW'] = s_clg_010_epw
df_summary

/var/folders/mk/7yynft554x38v3t6f_65fkzc0000gn/T/ipykernel_22460/539363201.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_summary['Heating DB 99.6% - EPW'] = s_htg_996_epw
/var/folders/mk/7yynft554x38v3t6f_65fkzc0000gn/T/ipykernel_22460/539363201.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_summary['Heating DB 99% - EPW'] = s_htg_990_epw
/var/folders/mk/7yynft554x38v3t6f_65fkzc0000gn/T/ipykernel_22460/539363201.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice

Location Name  \
1      Esperanza.Base-Hope.Bay ARG ATA                           
2      Esperanza.Base-Hope.Bay ARG ATA                           
3      Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   
4      Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   
5      Orcadas.Base-Laurie.Island-South.Orkney.Islands ARG ATA   
...                                                        ...   
30458  Montreal-Mirabel Intl AP QC CAN                           
30459  Slave Lake AB CAN                                         
30460  Wainwright CFB Airfield AB CAN                            
30461  Grand Etang NS CAN                                        
30462  Malay Falls NS CAN                                        

                              Coordinates  \
1      ['-56.99730', '-63.39810', '3.0']    
2      ['-56.99730', '-63.39810', '3.0']    
3      ['-44.73300', '-60.73300', '8.0']    
4      ['-44.73300', '-60.73300', '8.0']    
5      ['-44.73300', '-60.73300', '8.0']    
...                                  ...    
30458  ['-74.03860', '45.68060', '82.3']    
30459  ['-114.7800', '55.29000', '582.8']   
30460  ['-111.1000', '52.83000', '686.3']   
30461  ['-61.05000', '46.55000', '12.5']    
30462  ['-62.48000', '44.98000', '39.6']    

                                                                                                                                                  URL for files  \
1      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.2007-2021.zip                           
2      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Esperanza.Base-Hope.Bay.889630_TMYx.zip                                     
3      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2004-2018.zip   
4      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.2007-2021.zip   
5      https://climate.onebuilding.org/WMO_Region_7_Antarctica/ATA_Antarctica/ATA_ARG_Orcadas.Base-Laurie.Island-South.Orkney.Islands.889680_TMYx.zip             
...                                                                                                                                               ...             
30458  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/QC_Quebec/CAN_QC_Montreal-Mirabel.Intl.AP.719050_CWEC2016.zip            
30459  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/AB_Alberta/CAN_AB_Slave.Lake.713690_CWEC2020.zip                         
30460  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/AB_Alberta/CAN_AB_Wainwright.CFB.Airfield.711180_CWEC2020.zip            
30461  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NS_Nova_Scotia/CAN_NS_Grand.Etang.730300_CWEC2020.zip                    
30462  https://climate.onebuilding.org/WMO_Region_4_North_and_Central_America/CAN_Canada/NS_Nova_Scotia/CAN_NS_Malay.Falls.730290_CWEC2020.zip                    

          WMO last_year     Country State/Province         Station   WBAN  \
1      889630  2021      Antarctica  NaN            BASE ESPERANZA  99999   
2      889630  TMYx      Antarctica  NaN            BASE ESPERANZA  99999   
3      889680  2018      Antarctica  NaN            BASE ORCADAS    99999   
4      889680  2021      Antarctica  NaN            BASE ORCADAS    99999   
5      889680  TMYx      Antarctica  NaN            BASE ORCADAS    99999   
...       ...   ...             ...  ...                     ...      ...   
30458  719050  2016      Canada      QC             KUUJJUARAPIK    99999   
30459  713690  2020      Canada      AB             SLAVE LAKE      99999   
30460  711180  2020      Canada      AB             WAINWRIGHT CF

In [21]:
filename = 'AllRegion_Results.csv'
export_csv = df_summary.to_csv(filename, index = None, header=True) 